Optimization algorithm

In [ ]:
# Define the threshold ranges to try
threshold_ranges = {
    'TTdaysS2': [0, 1, 2, 3, 4, 5],
    'Ratio_stability_min': [0, 5, 10, 15, 20, 25, 30, 35, 40, 45, 50],
     'Ratio_stability_max': [0, 5, 10, 15, 20, 25, 30, 35, 40, 45, 50],
     'ConsecC_stability': [0, 1]}
    
# Define a list of threshold combinations to try
threshold_combinations = []
for tt in threshold_ranges['TTdaysS2']:
   for rsmin in threshold_ranges['Ratio_stability_min']:
         for rsmax in threshold_ranges['Ratio_stability_max']:
             for cs in threshold_ranges['ConsecC_stability']:
                 threshold_combinations.append((tt, rsmin, rsmax, cs))
    
# Evaluate each combination and save the performance metrics
performance = []
for combination in threshold_combinations:
    tt_threshold, rsmin_threshold, rsmax_threshold, cs_threshold = combination
        
# Apply the thresholds to the dataframe
    df['ChangeP1'] = np.nan
    df.loc[df['LC_20'] == 3, 'ChangeP1'] = 0
    df.loc[(df['LC_20'] == 3) & (df['TTdaysS2'] > tt_threshold), 'ChangeP1'] += 1.5
    df.loc[(df['LC_20'] == 3) & (df['Ratio_stability'] > rsmin_threshold) & (df['Ratio_stability'] < rsmax_threshold), 'ChangeP1'] += 1
    df.loc[(df['LC_20'] == 3) & (df['Ratio_stability'] > rsmax_threshold), 'ChangeP1'] +=1.5
    df.loc[(df['LC_20'] == 3) & (df['ConsecC_stability'] >= cs_threshold), 'ChangeP1'] +=1
    
    df['pred_changeP1'] = 0
    df.loc[df['ChangeP1'] >= 2.5, 'pred_changeP1'] += 1
        
    # Select the subset for which we want to optimize the detection (in this case, wintercrops: Winter Cereal and Spelt)
    subset = df.loc[(df['LC_20'] == 3) & (df['LC_21'] == 1) & ((df['CTL4A_21'] == 'WinterCereal') | (df['CTL4A_21'] == 'Spelt'))]
        
    # Evaluate the performance of the model on the subset (winter crops & spelt)
    true_change = subset['true_change']
    predicted_change = subset['pred_changeP1']
    tp = sum((predicted_change == 1) & (true_change == 1))
    tn = sum((predicted_change == 0) & (true_change == 0))
    fn = sum((predicted_change == 0) & (true_change == 1))
    
    recall = recall_score(true_change, predicted_change)
        
    # Evaluate the performance of the model on the subset (grasses to grasses)
    subset_g = df.loc[(df['LC_20'] == 3) & (df['LC_21'] == 3)]
    true_change = subset_g['true_change']
    predicted_change = subset_g['pred_changeP1']
    tp_g = sum((predicted_change == 1) & (true_change == 1))
    tn_g = sum((predicted_change == 0) & (true_change == 0))
    fp_g = sum((predicted_change == 1) & (true_change == 0))
   
    recall_g = recall_score(true_change, predicted_change)
           
    # Calculate the performance metric that reflects the desired optimization goal
    if len(subset_g) > 0 and (fp_g / len(subset_g)) <= 0.05:
            performance_metric = fn / tn_g
            performance.append((tt_threshold, rsmin_threshold, rsmax_threshold, cs_threshold,recall, performance_metric))

# Find the best performing combination of thresholds based on the performance metric
best_performance = min(performance, key=lambda x: x[‐1])
best_thresholds = best_performance[:4]
best_performance_metric = best_performance[‐1]
    
# Get the best threshold values
tt_threshold, rsmin_threshold, rsmax_threshold, cs_threshold = best_thresholds
    
# Apply the best thresholds to the dataframe
df['ChangeP1'] = np.nan
df.loc[df['LC_20'] == 3, 'ChangeP1'] = 0
df.loc[(df['LC_20'] == 3) & (df['TTdaysS2'] > tt_threshold), 'ChangeP1'] += 1.5
df.loc[(df['LC_20'] == 3) & (df['Ratio_stability'] > rsmin_threshold) &(df['Ratio_stability'] < rsmax_threshold), 'ChangeP1'] += 1
df.loc[(df['LC_20'] == 3) & (df['Ratio_stability'] > rsmax_threshold), 'ChangeP1'] += 1.5
df.loc[(df['LC_20'] == 3) & (df['ConsecC_stability'] >= cs_threshold), 'ChangeP1'] += 1
    
df['pred_changeP1'] = 0
df.loc[df['ChangeP1'] >= 2.5, 'pred_changeP1'] += 1
    
# Select the subset for which we want to optimize the detection (in this case, wintercrops: Winter Cereal and Spelt)
subset = df.loc[(df['LC_20'] == 3) & (df['LC_21'] == 1) & ((df['CTL4A_21'] == 'WinterCereal') | (df['CTL4A_21'] == 'Spelt'))]
   
# Evaluate the performance of the model on the subset (winter crops & spelt)
true_change = subset['true_change']
predicted_change = subset['pred_changeP1']
tp = sum((predicted_change == 1) & (true_change == 1))
tn = sum((predicted_change == 0) & (true_change == 0))
fn = sum((predicted_change == 0) & (true_change == 1))
    
# Evaluate the performance of the model on the subset (grasses to grasses)
subset_g = df.loc[(df['LC_20'] == 3) & (df['LC_21'] == 3)]
true_change = subset_g['true_change']
predicted_change = subset_g['pred_changeP1']
tp_g = sum((predicted_change == 1) & (true_change == 1))
tn_g = sum((predicted_change == 0) & (true_change == 0))
fp_g = sum((predicted_change == 1) & (true_change == 0))   
print("Best performance: Metric = {:.4f}, Recall = {:.4f}".format(best_performance_metric, best_performance[‐2]))
print("Best thresholds: tt_threshold = {}, rsmin_threshold = {}, rsmax_threshold = {}, cs_threshold = {}".format(tt_threshold, rsmin_threshold, rsmax_threshold, cs_threshold))
print("Best performance: tp = {}, tn = {}, fn = {}, tp_g = {}, tn_g = {}, fp_g ={}".format(tp, tn, fn, tp_g, tn_g, fp_g))